In [1]:
%autosave 0

Autosave disabled


In [3]:
#using my-work env from last module
!pip install grpcio==1.42.0 tensorflow-serving-api==2.7.0

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 4.0/4.0 MB 43.6 MB/s eta 0:00:00a 0:00:01
INFO: pip is looking at multiple versions of tensorboard to determine which version is compatible with other requirements. This could take a while.
  Using cached tensorflow-2.15.0.post1-cp310-cp310-manylinux_2_17_x86_64.manylinux2014_x86_64.whl.metadata (4.2 kB)
INFO: pip is still looking at multiple versions of tensorboard to determine which version is compatible with other requirements. This could take a while.
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 17.3/17.3 MB 96.1 MB/s eta 0:00:0000:0100:01
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 5.6/5.6 MB 107.5 MB/s eta 0:00:0000:01
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.7/1.7 MB 104.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 5.6/5.6 MB 132.9 MB/s eta 0:00:0000:01
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 440.7/440.7 kB 50.9 MB/s eta 0:00:00
INFO: This is taking longer than usual. You might need to provide the de

In [ ]:
#!pip install keras-image-helper

In [6]:
import grpc

import tensorflow as tf

from tensorflow_serving.apis import predict_pb2
from tensorflow_serving.apis import prediction_service_pb2_grpc


In [7]:
host = 'localhost:8500'

channel = grpc.insecure_channel(host)

stub = prediction_service_pb2_grpc.PredictionServiceStub(channel)

In [8]:
stub

In [9]:
from keras_image_helper import create_preprocessor

In [10]:
preprocessor = create_preprocessor('xception', target_size=(299, 299))

In [13]:
url = "https://raw.githubusercontent.com/alexeygrigorev/clothing-dataset-small/master/test/pants/0dfec862-c49f-430b-a6ef-c7ceb187225e.jpg"
X = preprocessor.from_url(url)

In [17]:
def np_to_protobuf(data):
    return tf.make_tensor_proto(data, shape=data.shape)

In [22]:
np_to_protobuf(X)

dtype: DT_FLOAT
tensor_shape {
  dim {
    size: 1
  }
  dim {
    size: 299
  }
  dim {
    size: 299
  }
  dim {
    size: 3
  }
}
tensor_content: "\254\253+\277\312\311I\277\320\317O\277\264\2633\277\322\321Q\277\334\333[\277\262\2611\277\320\317O\277\332\331Y\277\246\245%\277\312\311I\277\322\321Q\277\210\207\007\277\254\253+\277\264\2633\277\372\372\372\276\242\241!\277\252\251)\277\202\201\001\277\250\247\'\277\264\2633\277\246\245%\277\314\313K\277\330\327W\277\264\2633\277\332\331Y\277\346\345e\277\274\273;\277\342\341a\277\360\357o\277\274\273;\277\344\343c\277\362\361q\277\276\275=\277\344\343c\277\360\357o\277\304\303C\277\342\341a\277\354\353k\277\306\305E\277\340\337_\277\354\353k\277\306\305E\277\340\337_\277\354\353k\277\304\303C\277\342\341a\277\354\353k\277\304\303C\277\342\341a\277\360\357o\277\304\303C\277\342\341a\277\360\357o\277\302\301A\277\344\343c\277\364\363s\277\272\2719\277\340\337_\277\356\355m\277\264\2633\277\332\331Y\277\350\347g\277\256\255-\277\322\321

In [30]:
pb_request = predict_pb2.PredictRequest()

pb_request.model_spec.name = 'clothing-model'
pb_request.model_spec.signature_name = 'serving_default'

pb_request.inputs['input_22'].CopyFrom(np_to_protobuf(X))

In [31]:
pb_request

model_spec {
  name: "clothing-model"
  signature_name: "serving_default"
}
inputs {
  key: "input_22"
  value {
    dtype: DT_FLOAT
    tensor_shape {
      dim {
        size: 1
      }
      dim {
        size: 299
      }
      dim {
        size: 299
      }
      dim {
        size: 3
      }
    }
    tensor_content: "\254\253+\277\312\311I\277\320\317O\277\264\2633\277\322\321Q\277\334\333[\277\262\2611\277\320\317O\277\332\331Y\277\246\245%\277\312\311I\277\322\321Q\277\210\207\007\277\254\253+\277\264\2633\277\372\372\372\276\242\241!\277\252\251)\277\202\201\001\277\250\247\'\277\264\2633\277\246\245%\277\314\313K\277\330\327W\277\264\2633\277\332\331Y\277\346\345e\277\274\273;\277\342\341a\277\360\357o\277\274\273;\277\344\343c\277\362\361q\277\276\275=\277\344\343c\277\360\357o\277\304\303C\277\342\341a\277\354\353k\277\306\305E\277\340\337_\277\354\353k\277\306\305E\277\340\337_\277\354\353k\277\304\303C\277\342\341a\277\354\353k\277\304\303C\277\342\341a\277\360\357o\277

In [32]:
pb_response = stub.Predict(pb_request, timeout=20.0)

In [27]:
pb_response

outputs {
  key: "dense_20"
  value {
    dtype: DT_FLOAT
    tensor_shape {
      dim {
        size: 1
      }
      dim {
        size: 10
      }
    }
    float_val: -5.213781356811523
    float_val: -9.371926307678223
    float_val: -1.2359659671783447
    float_val: -2.6153476238250732
    float_val: 11.950028419494629
    float_val: -4.169875621795654
    float_val: -7.411005973815918
    float_val: 2.0846474170684814
    float_val: -6.824026584625244
    float_val: -8.505603790283203
  }
}
model_spec {
  name: "clothing-model"
  version {
    value: 1
  }
  signature_name: "serving_default"
}

In [36]:
preds = pb_response.outputs['dense_20'].float_val

In [38]:
classes = ['dress',
 'hat',
 'longsleeve',
 'outwear',
 'pants',
 'shirt',
 'shoes',
 'shorts',
 'skirt',
 't-shirt']
dict(zip(classes, preds))

{'dress': -5.213781356811523,
 'hat': -9.371926307678223,
 'longsleeve': -1.2359659671783447,
 'outwear': -2.6153476238250732,
 'pants': 11.950028419494629,
 'shirt': -4.169875621795654,
 'shoes': -7.411005973815918,
 'shorts': 2.0846474170684814,
 'skirt': -6.824026584625244,
 't-shirt': -8.505603790283203}